# Step 1: Set up D3 area

In [1]:
from IPython.core.display import display, HTML
from string import Template
import pandas as pd
import json, random

In [6]:
HTML('<script src="lib/d3/d3.min.js"></script>')
# HTML('<script src="https://d3js.org/d3.v4.min.js"></script>')

In [7]:
html_template = Template('''
<svg id="graph-div"></div>
<script> $js_text </script>
''')

In [8]:
js_text_template = Template('''
var data = $data;

var barHeight = 5;
var barWidth = 3;
var width = 800 * barWidth;

var x = d3.scale.linear()
        .domain([0, 1000])
        .range(["black", "white"]);

var chart = d3.select('#graph-div')
    .attr('width', width)
    .attr('height', 800);

function update() {    
    var row = chart.selectAll('.row')
        .data(data)
        .enter()
        .append('g')
        .attr('class', 'row')
        .attr('transform', function(d, i){
            return 'translate(0, ' + barHeight * i + ')';
        });

    var bar = row.selectAll('.bar')
        .data(function(d) { return d; })
        .enter()
        .append('g')
        .attr('class', "bar")
        .attr('transform', function(d, i){
            return 'translate(' + barWidth * i + ', 0)'
        })
        .append('rect')
        .attr('width', barWidth)
        .attr('height', barHeight)
        .attr('fill', function(d) {
            return x(d);
        });
}

update();
''')

In [9]:
data = [[]];
js_text = js_text_template.substitute({'data': json.dumps(data)})
HTML(html_template.substitute({'js_text': js_text}))

### OK, the D3 area is set up

Now we'll focus on live updating.  A manual test first.

In [6]:
js_text_template_2 = Template('''
data = $data;
update();
''')

In [7]:
# data = [2,2,5,0,1]
tests = [[500,500,500,500,1000,1000,1000,1000], [500,500,500,500,1000,1000,1000,1000]]

def update_graph(data):
    js_text = js_text_template_2.substitute({'data': json.dumps(tests)})
    display(HTML('<script>' + js_text + '</script>'))

update_graph(tests)

# Step 2: Now use MQTT to update the graph

Now for the fun stuff.  Using the `update_graph(data)` function set up above.  Each group of data, separated by `"start"` messages, is saved in the `tests` array.  As new data comes in, the live data graph is updated to show data from the last test.  All data is neatly saved inside the tests array for replotting and further analysis later.

Using the CloudMQTT free Cat plan:
* https://api.cloudmqtt.com/sso/cloudmqtt/console
* haipjacob@gmail.com:paramour-sieve-paper
* If the Websocket UI has trouble connecting, restart the instance

In [116]:
import paho.mqtt.client as mqtt

data = []
tests = [[]]

update_graph(tests)

def on_connect(client, userdata, flags, rc):
    print("Connected with result code "+str(rc))
    client.subscribe("/outTopic")

def on_message(client, userdata, msg):
    global data, tests
    try:
        msg_json = json.loads(msg.payload)
    except:
        print "Error"
        print(msg.topic+" "+str(msg.payload))
        return
    if msg_json['type'] == "BREAK" and msg_json['label'] == "LOOP":  # and msg_json['value'] == "END":
        tests.append(data)
        data = []
        update_graph(tests)
    if msg_json['type'] == "BINARY" and msg_json['label'] == "A0":
        data.append(int(msg_json['value']))
        tests[-1] = data
        update_graph(tests)

client = mqtt.Client()
client.on_connect = on_connect
client.on_message = on_message
client.username_pw_set("zettlmtm", "VOUbRcmhjffA")
client.connect("m11.cloudmqtt.com", 19280, 60)
client.loop_start()
# Make sure to call client.loop_stop() later

Connected with result code 0
Error
/outTopic hello world


Error
/outTopic hello world


Error
/outTopic hello world


Error
/outTopic hello world


Error
/outTopic hello world


Error
/outTopic hello world


Error
/outTopic hello world


Error
/outTopic hello world


Error
/outTopic hello world


Error
/outTopic hello world


In [115]:
client.loop_stop()

In [117]:
print tests

[[], [686, 791, 863, 856, 900, 896, 896, 918, 885, 909, 918, 889, 919, 896, 909, 909, 877, 916, 902, 902, 924, 892, 911, 903, 887, 909, 925, 926, 917, 895, 913, 872, 889, 919, 879, 916, 901, 885, 908, 876, 913, 902, 877, 921, 895, 893, 912, 921, 893, 925, 887, 906, 901, 873, 922, 894, 903, 918, 889, 917, 899, 891, 906, 893, 918, 908, 884, 915, 886, 906, 904, 869, 922, 902, 908, 912, 873], [662, 819, 858, 882, 915, 883, 919, 903, 886, 914, 883, 916, 910, 883, 925, 900, 901, 908, 873, 917, 909, 902, 920, 886, 918, 904, 882, 924, 894, 913, 910, 883, 920, 904, 909, 911, 870, 913, 900, 888, 916, 887, 917, 916, 890, 920, 887, 902, 909, 878, 921, 903, 893, 917, 889, 910, 905, 881, 911, 882, 909, 902, 881, 921, 900, 912, 929, 901, 915, 902, 889, 916, 880, 914, 906, 885, 915], [662, 819, 858, 882, 915, 883, 919, 903, 886, 914, 883, 916, 910, 883, 925, 900, 901, 908, 873, 917, 909, 902, 920, 886, 918, 904, 882, 924, 894, 913, 910, 883, 920, 904, 909, 911, 870, 913, 900, 888, 916, 887, 917, 916, 